In [1]:
import pandas as pd
import numpy as np
import os
from projdirs import datadir, optdir

DATA = pd.read_csv(datadir + r'TEST DATA\SAM_60min\086282TMY_60min_SAM.csv',skiprows=2)
solar = DATA['global horizontal irradiance'][0:1000].copy().tolist()
wind = DATA['wind speed'][0:1000].copy().tolist()


from PACKAGE.optimisation import make_dzn_file, optimise

simparams = dict(DT = 3600,#s
                 ETA_EL = 0.80,
                 C_PV = 0.6,#$/W
                 C_W = 1.6, #$/W
                 C_EL = 0.5, #$/W
                 C_HS = 16, #$/kgH 
                 CF = 0.99,
                 S = solar,
                 W = wind,
                 L = [0.1 for i in range(len(solar))])#kgH/s


results = optimise(simparams)

print ('CAPEX = %0.2f [M$]' %(float(results['CAPEX'][0])/1e6))
print ('pv_max = %0.2f [MW]' %(float(results['pv_max'][0]/1e6)))
print ('w_max = %0.2f [MW]' %(float(results['w_max'][0]/1e6)))
print ('el_max = %0.2f [MW]' %(float(results['el_max'][0]/1e6)))
print ('hs_max = %0.2f [t of H2]' %(float(results['hs_max'][0]/1e3)))

CAPEX = 88.13 [M$]
pv_max = 39.44 [MW]
w_max = 27.87 [MW]
el_max = 39.36 [MW]
hs_max = 12.52 [t of H2]


In [118]:
data_plot = pd.DataFrame(dict(t= np.arange(0,len(simparams['S'])),
                              solar=simparams['S'], wind=simparams['W'],
                              pv_out=results['pv_out'],
                              w_out=results['w_out'],
                              pc=results['pc'],
                              he_out = results['he_out'],
                              hr_out = results['hr_out'],
                              sh = results['sh'][0:-1],
                              R = results['r'][0:-1],
                              L = results['L'],
                              hs_out = results['L']-results['hr_out']
                             ))

data_plot['time'] =pd.to_datetime('2022-01-01') + pd.to_timedelta(data_plot.t, 'h')
data_plot.drop('t',axis=1,inplace=True)


data_plot

solar    wind        pv_out         w_out            pc    he_out  \
0      0.638560  4.0969  3.579919e+04  5.059530e+06  0.000000e+00  0.028706   
1      0.455680  3.9578  2.554651e+04  4.721795e+06  0.000000e+00  0.026746   
2      0.272800  3.8186  1.529382e+04  4.395495e+06  0.000000e+00  0.024850   
3      0.089916  3.6794  5.040905e+03  4.080876e+06  0.000000e+00  0.023019   
4      0.905500  4.4119  5.076449e+04  5.867468e+06  0.000000e+00  0.033342   
...         ...     ...           ...           ...           ...       ...   
8755  30.113000  5.2083  1.688206e+06  8.176951e+06  9.865158e+06  0.000000   
8756   1.370100  4.6539  7.681107e+04  6.528802e+06  6.605613e+06  0.000000   
8757   1.187200  4.5147  6.655726e+04  6.144085e+06  6.210642e+06  0.000000   
8758   1.004300  4.3756  5.630345e+04  5.771313e+06  0.000000e+00  0.032832   
8759   0.821440  4.2364  4.605188e+04  5.409951e+06  0.000000e+00  0.030738   

        hr_out           sh             R    L    hs_out                time  
0     0.065738    20.000000  31536.000000  0.1  0.034262 2022-01-01 00:00:00  
1     0.073254     0.000000  31299.341884  0.1  0.026746 2022-01-01 01:00:00  
2     0.075150     0.000000  31035.625991  0.1  0.024850 2022-01-01 02:00:00  
3     0.076981     0.000000  30765.084238  0.1  0.023019 2022-01-01 03:00:00  
4     0.066658     0.000000  30487.953547  0.1  0.033342 2022-01-01 04:00:00  
...        ...          ...           ...  ...       ...                 ...  
8755  0.000000  1577.579751      0.000000  0.1  0.100000 2022-12-31 19:00:00  
8756  0.000000  1217.579751      0.000000  0.1  0.100000 2022-12-31 20:00:00  
8757  0.000000   857.579751      0.000000  0.1  0.100000 2022-12-31 21:00:00  
8758  0.000000   497.579751      0.000000  0.1  0.100000 2022-12-31 22:00:00  
8759  0.000000   255.773670      0.000000  0.1  0.100000 2022-12-31 23:00:00  

[8760 rows x 12 columns]

In [120]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
#               line_shape='hv', name='Solar Irrad.'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.sh),
              name='Stored H',yaxis="y1"),
                )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.R),
              name='R',yaxis="y1")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.he_out),
              line_shape='hv',name='he_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hs_out),
              line_shape='hv',name='hs_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hr_out),
              line_shape='hv',name='hr_out',yaxis="y2")
                )



fig.update_layout(
    yaxis1=dict(
        range=[0, max(data_plot.sh)]
    ),
    yaxis2=dict(
        range=[0, 0.4]
    )
    
)
    

fig.show()

In [112]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
              line_shape='hv', name='Solar Irrad.', yaxis="y2"),
                )

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pv_out),
              line_shape='hv', name='pv_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.w_out),
              line_shape='hv', name='w_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pc),
              line_shape='hv', name='pc'),
                )




# fig.update_layout(
#     yaxis1=dict(
#         range=[0, 15000]
#     ),
#     yaxis2=dict(
#         range=[0, 0.4]
#     )
    
# )
    

fig.show()


In [32]:
results.keys()

dict_keys(['CAPEX', 'pv_max', 'w_max', 'el_max', 'hs_max', 'pv_out', 'w_out', 'pc', 'he_out', 'hr_out', 'sh', 'r', 'L'])